In [ ]:
%cd drive/MyDrive/InvdataExtract/


/content/drive/MyDrive/InvdataExtract


In [ ]:
!pip install opencv-contrib-python-headless
!pip install spacy
!spacy download en_core_web_lg

!pip install pytesseract
import pytesseract
!sudo apt install tesseract-ocr
pytesseract.pytesseract.tesseract_cmd = (
    r'/usr/bin/tesseract'
)


✔ Download and installation successful
You can now load the model via spacy.load('en_core_web_lg')
Reading package lists... Done
Building dependency tree       
Reading state information... Done
tesseract-ocr is already the newest version (4.00~git2288-10f4998a-2).
0 upgraded, 0 newly installed, 0 to remove and 15 not upgraded.


In [ ]:
import math
import cv2
from google.colab.patches import cv2_imshow
import numpy as np
import pytesseract
import Upscale as up
from pytesseract import Output
from collections import defaultdict
import spacy
# get grayscale image
def get_grayscale(image):
    return cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
# noise removal
def remove_noise(image):
    return cv2.medianBlur(image, 5)
# thresholding
def thresholding(image):
    return cv2.threshold(image, 0, 255, cv2.THRESH_BINARY + cv2.THRESH_OTSU)[1]
# dilation
def dilate(image):
    kernel = np.ones((5, 5), np.uint8)
    return cv2.dilate(image, kernel, iterations=1)
# erosion
def erode(image):
    kernel = np.ones((5, 5), np.uint8)
    return cv2.erode(image, kernel, iterations=1)
# opening - erosion followed by dilation
def opening(image):
    kernel = np.ones((5, 5), np.uint8)
    return cv2.morphologyEx(image, cv2.MORPH_OPEN, kernel)
# canny edge detection
def canny(image):
    return cv2.Canny(image, 100, 200)
# skew correction
def deskew(image):
    coords = np.column_stack(np.where(image > 0))
    angle = cv2.minAreaRect(coords)[-1]
    if angle < -45:
        angle = -(90 + angle)

    else:
        angle = -angle
        (h, w) = image.shape[:2]
        center = (w // 2, h // 2)
        M = cv2.getRotationMatrix2D(center, angle, 1.0)
        rotated = cv2.warpAffine(image, M, (w, h), flags=cv2.INTER_CUBIC, borderMode=cv2.BORDER_REPLICATE)
        return rotated
# template matching
def match_template(image, template):
    return cv2.matchTemplate(image, template, cv2.TM_CCOEFF_NORMED)

#TODO: SuperResoultion model and better preprocesing of images more suited to Data Extraction

def centre_position(left, top, width, height):
    return [left+width/2,top+height/2]
#Top line positions
def lt_position(left, top, width, height):
    return [left,top]

def rt_position(left, top, width, height):
    return [left+width,top]

def ct_position(left, top, width, height):
    return [left+width/2,top]
#Bottom line positions
def lb_position(left, top, width, height):
    return [left,top+height]

def rb_position(left, top, width, height):
    return [left+width,top+height]

def cb_position(left, top, width, height):
    return [left+width/2,top+height]
# Centre line positions
def cl_position(left, top, width, height):
    return [left,top+height/2]

def cr_position(left, top, width, height):
    return [left+width,top+height/2]


In [ ]:

class Rect:
    def __init__(self,cpt,w,h,text,conf):
        self.x = cpt[0]
        self.y = cpt[1]
        self.w = w
        self.h = h
        self.t = text
        self.left = self.x-self.w/2
        self.top = self.y-self.h/2
        self.lt = lt_position(self.left,self.top,self.w,self.h)
        self.rt = rt_position(self.left,self.top,self.w,self.h)
        self.lb = lb_position(self.left, self.top, self.w, self.h)
        self.rb = rb_position(self.left, self.top, self.w, self.h)
        self.conf = conf

    def combine(self,other):
        new_top= min(self.top, other.top)
        new_left = min(self.left,other.left)
        new_rb_top = max(self.rb[1],other.rb[1])
        new_rb_left = max(self.rb[0],other.rb[0])
        new_x = (new_left+new_rb_left)/2
        new_y = (new_top+new_rb_top)/2
        new_w = new_rb_left-new_left
        new_h = new_rb_top-new_top

        
        if (self.x<other.x):
                  new_t = self.t+" "+other.t
        else:
          new_t = other.t+" "+self.t

        new_conf = min(self.conf,other.conf)

        new_rect = Rect((new_x,new_y),new_w,new_h, new_t,new_conf)
        return new_rect

    def order(self,other):
      if (self.top==other.top):
        if (self.left<other.left):
          return self
        else:
          return other
      elif (self.top<other.top) and ((other.top-self.top)>0.5*max(self.h,other.h)):
        return self
      elif (self.top<other.top) and ((other.top-self.top)<0.5*max(self.h,other.h)) and (other.left<self.left):
        return other
      elif (self.top<other.top) and ((other.top-self.top)<0.5*max(self.h,other.h)) and (other.left>self.left):
        return self

      elif (self.top>other.top) and ((self.top-other.top)>0.5*max(self.h,other.h)):
        return other
      elif (self.top>other.top) and ((self.top-other.top)<0.5*max(self.h,other.h)) and (other.left>self.left):
        return self
      elif (self.top>other.top) and ((self.top-other.top)<0.5*max(self.h,other.h)) and (other.left<self.left):
        return other
      else:
        return self
    def hdist(self,other):
        if abs(self.x - other.x) <= (self.w + other.w)/2 :
            dx = 0;
        else:
            dx = abs(self.x - other.x) - (self.w + other.w)/2
        return dx

    def vdist(self,other):
        if abs(self.y - other.y) <= (self.h + other.h)/2:
            dy = 0;
        else:
          dy = abs(self.y - other.y) - (self.h + other.h)/2
        return dy

# This class represents a
# directed graph using adjacency
# list representation


class Graph:

    # Constructor
    def __init__(self):
        # default dictionary to store graph
        self.graph = defaultdict(list)
        self.block = []

    # function to add an edge to graph
    def addEdge(self, u, v):
        self.graph[u].append(v)
        self.graph[v].append(u)
    
    def selective(self):
      hor = dict()
      ver = dict()
      new_ed = defaultdict(list)
      for ref in self.graph: 
              hor[ref] = sorted(self.graph[ref], key = ref.hdist)
             
              ver[ref] = sorted(self.graph[ref], key = ref.vdist)
      for key in hor:
          count =0
          of = 0
          tf = 0
          for i in range(len(hor[key])):
              #wanted--key --- wanted
            if count<2:
                if (hor[key][i].vdist(key)==0 and (hor[key][i].x<key.x) and (of==0)):
                  new_ed[key].append(hor[key][i])
                  count+=1
                  of=1
                if (hor[key][i].vdist(key)==0 and (hor[key][i].x>key.x) and (tf==0)):
                  new_ed[key].append(hor[key][i])
                  count+=1
                  tf=1
            else:
                break
      for key in ver:
          count =0
          of = 0
          tf = 0
          for i in range(len(ver[key])):
              #wanted
              # |
              #key
              # |
              #wanted
            if count<2:
                if (ver[key][i].hdist(key)==0 and (ver[key][i].y<key.y)and (of==0)): 
                  new_ed[key].append(ver[key][i])
                  count+=1
                  of=1
                if (ver[key][i].hdist(key)==0 and (ver[key][i].y>key.y) and (tf==0)):
                  new_ed[key].append(ver[key][i])
                  count+=1
                  tf=1
            else:
                break
      self.graph = new_ed
      

    # A function used by DFS
    def DFSUtil(self, v, visited,x_var=None,y_var=None):

        # Mark the current node as visited and print it
        visited.add(v)


        # Recur for all the vertices adjacent to
        # this vertex
        for neighbour in self.graph[v]:
          if x_var!=None:
            if (neighbour not in visited) and (neighbour.hdist(v)<=x_var) and (neighbour.vdist(v)<=y_var) :
                self.block[-1]= self.block[-1].combine(neighbour)
                self.DFSUtil(neighbour, visited,x_var,y_var)
            
          elif x_var==None:
            if neighbour not in visited:
                self.block[-1]= self.block[-1].combine(neighbour)
                self.DFSUtil(neighbour, visited)
                

    def DFS(self,x_var=None,y_var=None):
        #self.graph = sorted(self.graph.keys(),key=functools.cmp_to_key(order), reverse=True)
        visited = set()

        for vertex in list(self.graph):
            if vertex not in visited:
                self.block.append(vertex)
                self.DFSUtil(vertex, visited,x_var,y_var)
        
        return self.block



In [ ]:
def adj_matrix(data,height,width,x_thresh,y_thresh):

    size = len(data)
    
    edges = []
    single = []
    used = [0]*size
    data.sort(key = functools.cmp_to_key(order),reverse = True)

    for i in range(size):
        for j in range(size):
            if j>i:
                hdist = data[i].hdist(data[j])
                vdist = data[i].vdist(data[j])
                if (hdist<=x_thresh*width) and (vdist<=y_thresh*height):
                    used[i]=1
                    used[j]=1
                    edges.append([data[i],data[j]])

    for i in range(size):
        if used[i] == 0:
            single.append(data[i])

    
    g = Graph()
    edges.sort(key = functools.cmp_to_key(order_ed),reverse = True)
    for i in edges:
        g.addEdge(i[0],i[1])
    
    g.selective()    
    
    return edges, g, single

def show_boxes(data,image,color1,data2 = None,color2= None):
    for o in data:
        (x, y, w, h) = (int(o.x - (o.w) / 2), int(o.y - (o.h) / 2), int(o.w), int(o.h))
        img = cv2.rectangle(image, (x, y), (x + w, y + h), color1, 2)
        #print(o.t)
        img = cv2.putText(image, o.t, (x,y-10), cv2.FONT_HERSHEY_SIMPLEX,1.2, (255, 0, 0), 3)
    if (data2 != None) and (color2 != None):
        for o in data2:
            (x, y, w, h) = (int(o.x - (o.w) / 2), int(o.y - (o.h) / 2), int(o.w), int(o.h))
            img = cv2.rectangle(image, (x, y), (x + w, y + h), color2, 2)

    return img


In [ ]:
import Upscale as up
import functools
#im4 = up.super_resolve('excel-ss.png')
#im = up.super_resolve('0000037010.tif')

#im2 = up.super_resolve('0000020180.tif')
#upscaletest = up.super_resolve('test2.png')

#test = up.super_resolve('test.png')

# Applying Multiple OCRs with different preprocessed images and combining results for better accuracy

def show_layer(g,im,data,sin):
  L = g.graph
  for c in L:
    for v in L[c]:
      cv2.line(im,(int(c.x),int(c.y)),(int(v.x),int(v.y)),(255,0,0),2)
  
  process2img = show_boxes(data, im,(0,255,0),sin,(255,0,0)) 
  cv2_imshow(process2img)
def combine_ocr(pos1,pos2,pos3,pos4):
  combined_posxy = pos1+pos2
  combined2_posxy = pos3 + pos4
  final1_posxy=[]
  final2_posxy =[]
  use1 = [0]*len(combined_posxy)
  use2 = [0]*len(combined2_posxy)
  for i in range(len(combined_posxy)):
          for j in range(len(combined_posxy)):
              if j>i:
                box = combined_posxy[i]
                box2 = combined_posxy[j]

                if (box.hdist(box2)==0) and (box.vdist(box2)==0) and (use1[i]==0) and (use1[j]==0):
                  if box.conf>box2.conf:
                    final1_posxy.append(box)
                  else:
                    final1_posxy.append(box2)
                  use1[i]=1
                  use1[j]=1
                  break
              if (j == len(combined_posxy)-1) and (use1[i]==0):
                final1_posxy.append(combined_posxy[i])

  for i in range(len(combined2_posxy)):
          for j in range(len(combined2_posxy)):
              if j>i:
                box = combined2_posxy[i]
                box2 = combined2_posxy[j]
                if (box.hdist(box2)==0) and (box.vdist(box2)==0) and (use2[i]==0) and (use2[j]==0):
                  if box.conf>box2.conf:
                    final2_posxy.append(box)
                  else:
                    final2_posxy.append(box2)
                  use2[i]=1
                  use2[j]=1
                  break
              if (j == len(combined2_posxy)-1) and (use2[i]==0):
                final2_posxy.append(combined2_posxy[i])

  combined3_posxy = final1_posxy +final2_posxy
  final_posxy = []
  final_use = [0]*len(combined3_posxy)
  for i in range(len(combined3_posxy)):
          for j in range(len(combined3_posxy)):
              if j>i:
                box = combined3_posxy[i]
                box2 = combined3_posxy[j]
                if (box.hdist(box2)==0) and (box.vdist(box2)==0)and (final_use[i]==0) and (final_use[j]==0):
                  if box.conf>box2.conf:
                    final_posxy.append(box)
                  else:
                    final_posxy.append(box2)
                  final_use[i]=1
                  final_use[j]=1
                  break
              if (j == len(combined3_posxy)-1) and (final_use[i]==0) :
                final_posxy.append(combined3_posxy[i])
  final_posxy.sort(key = functools.cmp_to_key(order),reverse = True)
  removed_duplicates =[]
  keep = [0]*len(final_posxy)
  for i in range(len(final_posxy)):

      for j in range(len(final_posxy)):
        box2 = final_posxy[j]
        box = final_posxy[i]
        if (box.hdist(box2)==0) and (box.vdist(box2)==0) and (box.t==box2.t):
          if (box.w*box.h<=box2.w*box2.h):
            keep[j]=0
            keep[i]=1
          else:
            keep[i]=0
            keep[j]=1
          break
        if (j==len(final_posxy)-1):
          keep[i]=1
  for i in range(len(keep)):
    if (keep[i]==1):
      removed_duplicates.append(final_posxy[i])      

          
  removed_duplicates.sort(key = functools.cmp_to_key(order),reverse = True)  
     
    
  return removed_duplicates
def order(self,other):
  
      if (self.top==other.top):
        if (self.left<other.left):
          return 1
        else:
          return -1
      elif (self.top<other.top) and ((other.top-self.top)>0.5*max(self.h,other.h)):
        return 1
      elif (self.top<other.top) and ((other.top-self.top)<0.5*max(self.h,other.h)) and (other.left<self.left):
        return -1
      elif (self.top<other.top) and ((other.top-self.top)<0.5*max(self.h,other.h)) and (other.left>self.left):
        return 1

      elif (self.top>other.top) and ((self.top-other.top)>0.5*max(self.h,other.h)):
        return -1
      elif (self.top>other.top) and ((self.top-other.top)<0.5*max(self.h,other.h)) and (other.left>self.left):
        return 1
      elif (self.top>other.top) and ((self.top-other.top)<0.5*max(self.h,other.h)) and (other.left<self.left):
        return -1
      else:
        return 0       
def order_ed(self,other):
      if (self[0].top==other[0].top):
        if (self[0].left<other[0].left):
          return 1
        else:
          return -1
      elif (self[0].top<other[0].top) and ((other[0].top-self[0].top)>0.5*max(self[0].h,other[0].h)):
        return 1
      elif (self[0].top<other[0].top) and ((other[0].top-self[0].top)<0.5*max(self[0].h,other[0].h)) and (other[0].left<self[0].left):
        return -1
      elif (self[0].top<other[0].top) and ((other[0].top-self[0].top)<0.5*max(self[0].h,other[0].h)) and (other[0].left>self[0].left):
        return 1

      elif (self[0].top>other[0].top) and ((self[0].top-other[0].top)>0.5*max(self[0].h,other[0].h)):
        return -1
      elif (self[0].top>other[0].top) and ((self[0].top-other[0].top)<0.5*max(self[0].h,other[0].h)) and (other[0].left>self[0].left):
        return 1
      elif (self[0].top>other[0].top) and ((self[0].top-other[0].top)<0.5*max(self[0].h,other[0].h)) and (other[0].left<self[0].left):
        return -1
      else:
        return 0
def make_rects(image,original):
  h, w= image.shape
  custom_config = r'--oem 3 --psm 4'

  d = pytesseract.image_to_data(image, output_type=Output.DICT, config = custom_config)
  n_boxes = len(d['text'])
  posxy = []
  unsure = []
  for i in range(n_boxes):
      (x, y, w, h) = (d['left'][i], d['top'][i], d['width'][i], d['height'][i])
      cpos = centre_position(d['left'][i],d['top'][i],d['width'][i],d['height'][i])
      A = Rect((cpos[0],cpos[1]),w,h,d['text'][i],d['conf'][i])

      if int(d['conf'][i]) > 60:
          if (d['text'][i]==' ') or (d['text'][i]=='???'):
              unsure.append(A)
          else:
              posxy.append(A)
      else:
        unsure.append(A)
  
  image = original
  return posxy,unsure
def Optimal_ocr(im): 
  gray = get_grayscale(im)
  thresh = thresholding(gray)
  openim = opening(gray)
  canned = canny(gray)
  grayposxy,gray_unsure =make_rects(gray,im)
  threshposxy,thresh_unsure = make_rects(thresh,im)
  openingposxy,opening_unsure = make_rects(openim,im)
  cannyposxy,canny_unsure = make_rects(canned,im)
  posxy = combine_ocr(grayposxy,threshposxy,openingposxy,cannyposxy)
  
  return posxy
def Clustering(im):
  h,w,c = im.shape
  Optimized_OCR = Optimal_ocr(im)
  # HL 1 achieved with multiple layered OCR with 4 different preprocessed images
  ed, graphing, one_word = adj_matrix(Optimized_OCR,h,w,0.5,0.05)
  imcopy = im.copy()
  show_layer(graphing,imcopy,Optimized_OCR,one_word)
  # HL 2 created with help of HL1 graph and data
  small_line_data = graphing.DFS(0.04*w,0)+one_word 
  
  #HL2 data converted into HL2 graph 
  ed2, small_line_graph,one_word2 = adj_matrix(small_line_data,h,w,0.5,0.05)
  #showlayer to see HL2 graph
  show_layer(small_line_graph,im,small_line_data,one_word2)
  

  

  #HL3 created with HL2 graph /// DOESNT WORK WELL WITH VERTICAL GROUPING, THE ORDERING OF WORDS IS OFF AND BOXES ARE BEING DRAWN WITHNIN OTHER ONES
  #chunk_data = small_line_graph.DFS(0,0.03*h)+one_word2
  #ed3,chunk_graph,one_word3 = adj_matrix(chunk_data,h,w,0.25,0.05)
  #show_layer(chunk_graph,im,chunk_data,one_word3)
  
  return graphing, small_line_graph,Optimized_OCR, small_line_data


G1,G2,G1_data,G2_data = Clustering(up.super_resolve('t3.png'))
'''
Clustering(up.super_resolve('t1.png'))
Clustering(up.super_resolve('t12.png'))
Clustering(up.super_resolve('t11.png'))
Clustering(up.super_resolve('t10.png'))
Clustering(up.super_resolve('t13.png'))
Clustering(up.super_resolve('t9.png'))
Clustering(up.super_resolve('t8.png'))
Clustering(up.super_resolve('t7.png'))
Clustering(up.super_resolve('t6.png'))
Clustering(up.super_resolve('t5.png'))
Clustering(up.super_resolve('t4.png'))
Clustering(up.super_resolve('t3.png'))
Clustering(up.super_resolve('t2.png'))
Clustering(up.super_resolve('test.png'))
Clustering(up.super_resolve('test2.png'))
Clustering(up.super_resolve('test.jpg'))
Clustering(up.super_resolve('test2.jpg'))
Clustering(up.super_resolve('test3.jpg'))
Clustering(up.super_resolve('test4.jpg'))
Clustering(up.super_resolve('test5.jpg'))
Clustering(up.super_resolve('test6.jpg'))
'''





"\nClustering(up.super_resolve('t1.png'))\nClustering(up.super_resolve('t12.png'))\nClustering(up.super_resolve('t11.png'))\nClustering(up.super_resolve('t10.png'))\nClustering(up.super_resolve('t13.png'))\nClustering(up.super_resolve('t9.png'))\nClustering(up.super_resolve('t8.png'))\nClustering(up.super_resolve('t7.png'))\nClustering(up.super_resolve('t6.png'))\nClustering(up.super_resolve('t5.png'))\nClustering(up.super_resolve('t4.png'))\nClustering(up.super_resolve('t3.png'))\nClustering(up.super_resolve('t2.png'))\nClustering(up.super_resolve('test.png'))\nClustering(up.super_resolve('test2.png'))\nClustering(up.super_resolve('test.jpg'))\nClustering(up.super_resolve('test2.jpg'))\nClustering(up.super_resolve('test3.jpg'))\nClustering(up.super_resolve('test4.jpg'))\nClustering(up.super_resolve('test5.jpg'))\nClustering(up.super_resolve('test6.jpg'))\n"

In [ ]:
import spacy
from spacy import displacy
from spacy.tokens import Doc
from spacy.tokens import Token
import re
class word:
  def __init__(self,t,r):
    self.characters = t
    self.contained = r
  

nlp = spacy.load('en_core_web_lg')
word_container = []
org_container = []
name_container = []
date_container = []
address_container = []
money_container = []
email_container = []
phone_container = []
fullText = '' 
for line in G2_data:
  s = line.t
  regex = r"\S+@\S+"
  regex2 = re.compile(r'''(
    [(]?(\d{3})?[)]? # area code
    (\s|-|\.)? # separator
    (\d{3}) # first 3 digits
    (\s|-|\.) # separator
    (\d{4}) # last 4 digits
    (\s|,) # separator
    (\s*(ext|x|ext.)\s*(\d{2,5}))? # extension
  )''', re.VERBOSE | re.IGNORECASE)

  match = re.search(regex,s)
  if match!= None:
    A = word(match.group(0),line)
    email_container.append(A)
    
  
  match2 = regex2.fullmatch(s)
  if match2!= None:
    A = word(match2.group(0),line)
    phone_container.append(A) 
    
  if line!=G2_data[-1]:
    fullText += line.t+' '
  else:
    fullText += line.t
  for w in nlp(line.t):
    A = word(w.text,line)
    word_container.append(A)
  for ent in nlp(line.t).ents:
    #print(ent.text, ent.start_char, ent.end_char, ent.label_)
    A = word(ent.text,line)
    if (ent.label_== "ORG"):
      org_container.append(A)
    elif (ent.label_== "PERSON"):
      name_container.append(A)
    elif (ent.label_== "GPE"):
      address_container.append(A)
    elif (ent.label_== "LOC"):
      address_container.append(A)
    elif (ent.label_== "MONEY"):
      money_container.append(A)
    elif (ent.label_== "DATE"):
      date_container.append(A)

    

doc = (nlp(fullText))


for x in org_container:
  print(x.characters)
for x in name_container:
  print(x.characters)
for x in address_container:
  print(x.characters)
for x in money_container:
  print(x.characters)
for x in date_container:
  print(x.characters)
for x in email_container:
  print(x.characters)
for x in phone_container:
  print(x.characters)
#for ent in doc.ents:
  #print(ent.text, ent.start_char, ent.end_char, ent.label_)
    #print(token.text, token.lemma_, token.pos_, token.tag_, token.dep_,
            #token.shape_, token.is_alpha, token.is_stop)

#displacy.render(doc,style="dep")



Holbrook
Kohler
Bill
Jenn Rogers
Deerfield
Toledo
Highland St.
Toledo
268.00
268.00
540.00
540.00
75.00
75.00
883.00
200.00
600.00
200.00
1,200.00
75.00
75.00
1,875.00
2,758.00
220.64
2,978.64
0.00
2,978.64
OH 43612
3 days
service@holbrookconstruction.com
jenn_rogers@yahoo.com
